In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import sklearn.metrics as metrics
import numpy as np
from sklearn.neighbors import NearestNeighbors
from scipy.spatial.distance import correlation, cosine
import ipywidgets as widgets
from IPython.display import display, clear_output
from sklearn.metrics import pairwise_distances
from sklearn.metrics import mean_squared_error
from math import sqrt
import sys, os
from contextlib import contextmanager
global k,metric

In [45]:
customer=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//target_customer.csv')

In [38]:
appearance=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//product_appearance.csv')

In [10]:
incremental=pd.read_csv('C://Users//Jacky Yang//Desktop//Marketing Analytics//Recommend System//incremental_sales.csv')

In [11]:
incremental.head(5)

Unnamed: 0    prod_id  avg_sales_np  avg_sales  incremental
0           1  145519008     63.236701  59.446269    -3.790432
1           2  145519009     43.003038  52.952610     9.949572
2           3  145519010     29.132745  56.229481    27.096736
3           4  145519011    119.144836  64.283540   -54.861296
4           5  145519012     79.957492  54.581208   -25.376284

In [ ]:
appearance.head(5)

In [69]:
appearance['N'].describe()

count     6852.000000
mean       312.354787
std       1363.508309
min          1.000000
25%         39.000000
50%         96.000000
75%        246.000000
max      73374.000000
Name: N, dtype: float64

In [46]:
#filter out products that are bought less than 15 times
appearance_filtered=appearance[appearance['N']>15]
customer=customer[customer['prod_id'].isin(appearance_filtered['prod_id'])]

In [ ]:
#only select the promoted products

In [19]:
pd.set_option('display.max_colwidth', 1000)
pd.set_option('display.max_rows', 1000)

In [47]:
customer=customer[customer['brand_desc']!='PRIVATE LABEL']
customer=customer[customer['brand_desc']!='NO LABEL']

In [48]:
customer['rating']=1

In [ ]:
all_prod=list(customer['prod_id'].unique())
all_cust=list(customer['cust_id'].unique())

In [ ]:
len(all_prod)

In [ ]:
len(all_cust)

In [49]:
customer

Unnamed: 0    prod_id   cust_id       tran_id     tran_dt  store_id  \
0                 1  145519008    799924  2.017111e+18  2017-11-12       349   
1                 2  145519008   1889991  2.017111e+18  2017-11-07       554   
2                 3  145519008   1889991  2.017111e+18  2017-11-13       554   
3                 4  145519008   2109544  2.017112e+18  2017-11-25       174   
4                 5  145519008   7629630  2.017103e+18  2017-10-30       506   
5                 6  145519008   7669833  2.017111e+18  2017-11-11       625   
6                 7  145519008   7739787  2.017122e+18  2017-12-19       585   
7                 8  145519008   8639635  2.017103e+18  2017-10-28       313   
8                 9  145519008   8639635  2.017111e+18  2017-11-11       313   
9                10  145519008  10329832  2.017120e+18  2017-12-01       986   
10               11  145519008  11789884  2.017111e+18  2017-11-12       343   
11               12  145519008  16739664  2.017102e+18  2017-10-20       296   
12               13  145519008  16829885  2.017111e+18  2017-11-12       339   
13               14  145519008  18409710  2.017112e+18  2017-11-24       522   
14               15  145519008  18539540  2.017103e+18  2017-10-29       631   
15               16  145519008  18539540  2.017110e+18  2017-11-01       266   
16               17  145519008  18539540  2.017112e+18  2017-11-17       266   
17               18  145519008  18539540  2.017120e+18  2017-12-05       266   
18               19  145519008  18539540  2.017123e+18  2017-12-28       266   
19               20  145519008  18909750  2.017102e+18  2017-10-24       687   
20               21  145519008  18909750  2.017111e+18  2017-11-11       687   
21               22  145519008  18909750  2.017112e+18  2017-11-24       349   
22               23  145519008  21159716  2.017103e+18  2017-10-25       638   
23               24  145519008  21579922  2.017122e+18  2017-12-23       993   
24               25  145519008  24179544  2.017120e+18  2017-12-05       179   
25               26  145519008  26499927  2.017102e+18  2017-10-23       519   
26               27  145519008  26769899  2.017111e+18  2017-11-13       664   
27               28  145519008  27999642  2.017103e+18  2017-10-29       554   
28               29  145519008  28659946  2.017112e+18  2017-11-15       182   
29               30  145519008  31879773  2.017111e+18  2017-11-09       625   
30               31  145519008  37359574  2.017103e+18  2017-10-28       608   
31               32  145519008  37449943  2.017103e+18  2017-10-27       316   
32               33  145519008  37719816  2.017111e+18  2017-11-11       395   
33               34  145519008  38479729  2.017103e+18  2017-10-30       307   
34               35  145519008  38959697  2.017111e+18  2017-11-10       321   
35               36  145519008  38959697  2.017113e+18  2017-11-27       321   
36               37  145519008  38959697  2.017120e+18  2017-12-05       321   
37               38  145519008  41459822  2.017103e+18  2017-10-27       398   
38               39  145519008  41579936  2.017112e+18  2017-11-22       180   
39               40  145519008  41709604  2.017111e+18  2017-11-08       572   
40               41  145519008  41709665  2.017112e+18  2017-11-24       596   
41               42  145519008  42469999  2.017122e+18  2017-12-19       510   
42               43  145519008  43769997  2.017111e+18  2017-11-07       179   
43               44  145519008  46619809  2.017111e+18  2017-11-10       335   
44               45  145519008  47779590  2.017122e+18  2017-12-20       606   
45               46  145519008  50759829  2.017112e+18  2017-11-23       656   
46               47  145519008  50759829  2.017121e+18  2017-12-05       656   
47               48  145519008  50759829  2.017122e+18  2017-12-19       656   
48               49  145519008  51079908  2.017112e+18  2017-11-25       344   
49       

In [29]:
len(customer['prod_id'].unique())

622

In [ ]:
p=list()

In [ ]:
for p_i in range(len(all_prod)):
    for c_i in range(len(all_cust)):
        #all the products for a single customer
        c=customer[customer['cust_id']==all_cust[c_i]]
        if all_prod[p_i] in c['prod_id']:
                   p.append(1)
        else:
                   p.append(0)
                   

In [50]:
m=pd.pivot_table(customer,index ='cust_id', columns ='prod_id', values = 'rating').fillna(0)

In [51]:
m

prod_id   145519008  145519009  145519010  145519011  145519012  148066012  \
cust_id                                                                      
29568           0.0        0.0        0.0        0.0        0.0        0.0   
29909           0.0        0.0        0.0        0.0        0.0        0.0   
39856           0.0        0.0        0.0        0.0        0.0        0.0   
109693          0.0        0.0        0.0        0.0        0.0        0.0   
289996          0.0        0.0        0.0        0.0        0.0        0.0   
299749          0.0        0.0        0.0        0.0        0.0        0.0   
329968          0.0        0.0        1.0        0.0        0.0        0.0   
339627          0.0        0.0        0.0        0.0        0.0        0.0   
550000          0.0        0.0        0.0        1.0        1.0        0.0   
559804          0.0        0.0        0.0        0.0        0.0        0.0   
609881          0.0        0.0        0.0        0.0        0.0        0.0   
709543          0.0        0.0        0.0        0.0        0.0        0.0   
749556          0.0        0.0        0.0        0.0        1.0        0.0   
749639          0.0        0.0        0.0        0.0        0.0        0.0   
769883          0.0        0.0        0.0        0.0        0.0        0.0   
799924          1.0        0.0        0.0        0.0        1.0        0.0   
869947          0.0        0.0        0.0        0.0        0.0        0.0   
989587          0.0        0.0        0.0        0.0        0.0        0.0   
1049570         0.0        0.0        0.0        0.0        0.0        0.0   
1139738         0.0        0.0        1.0        0.0        0.0        0.0   
1179795         0.0        0.0        0.0        0.0        0.0        1.0   
1279966         0.0        0.0        1.0        0.0        0.0        0.0   
1329967         0.0        0.0        0.0        0.0        0.0        0.0   
1369576         0.0        0.0        0.0        0.0        0.0        0.0   
1459955         0.0        0.0        0.0        0.0        1.0        1.0   
1539803         0.0        0.0        0.0        0.0        0.0        0.0   
1589813         0.0        0.0        0.0        0.0        0.0        0.0   
1659549         0.0        0.0        0.0        0.0        0.0        0.0   
1849794         0.0        0.0        0.0        0.0        0.0        0.0   
1889991         1.0        1.0        1.0        0.0        0.0        0.0   
1979644         0.0        0.0        0.0        0.0        0.0        0.0   
1999671         0.0        0.0        0.0        1.0        0.0        1.0   
2009974         0.0        0.0        0.0        0.0        0.0        0.0   
2029760         0.0        1.0        0.0        0.0        0.0        0.0   
2039621         0.0        0.0        0.0        0.0        0.0        0.0   
2049977         0.0        0.0        0.0        0.0        0.0        0.0   
2089806         0.0        0.0        0.0        0.0        0.0        0.0   
2109544         1.0        0.0        1.0        1.0        0.0        0.0   
2169803         0.0        0.0        0.0        0.0        1.0        0.0   
2209804         0.0        0.0        0.0        0.0        0.0        0.0   
2269534         0.0        0.0        0.0        0.0        0.0        1.0   
2389981         0.0        0.0        0.0        0.0        0.0        0.0   
2469932         0.0        0.0        0.0        0.0        0.0        0.0   
2499933         0.0        0.0        0.0        0.0        0.0        0.0   
2569933         0.0        0.0        0.0        0.0        0.0        0.0   
2589576         0.0        0.0        0.0        0.0        0.0        0.0   
2629968         0.0        0.0        0.0        0.0        0.0        0.0   
2679893         0.0        0.0        0.0        0.0        0.0        0.0   
2719577         0.0        0.0        0.0        0.0        0.0        0.0   
2809801         0.0   

In [56]:
cosine_sim = pd.DataFrame(1-pairwise_distances(m, metric="cosine"))

In [57]:
cosine_sim

0         1         2         3         4         5         6     \
0     1.000000  0.211481  0.265617  0.218605  0.189003  0.244841  0.230289   
1     0.211481  1.000000  0.229511  0.183954  0.209875  0.188116  0.212436   
2     0.265617  0.229511  1.000000  0.152898  0.196476  0.237962  0.264481   
3     0.218605  0.183954  0.152898  1.000000  0.171523  0.152504  0.152074   
4     0.189003  0.209875  0.196476  0.171523  1.000000  0.143769  0.203972   
5     0.244841  0.188116  0.237962  0.152504  0.143769  1.000000  0.197323   
6     0.230289  0.212436  0.264481  0.152074  0.203972  0.197323  1.000000   
7     0.223682  0.208603  0.222311  0.158337  0.194346  0.196598  0.193710   
8     0.254526  0.187471  0.218131  0.156570  0.203145  0.193756  0.230302   
9     0.214676  0.182193  0.196936  0.192995  0.178584  0.187363  0.153336   
10    0.191714  0.195148  0.193986  0.177482  0.131281  0.161565  0.177891   
11    0.275747  0.201915  0.229711  0.166103  0.156910  0.229315  0.212621   
12    0.258722  0.202267  0.204305  0.216512  0.182537  0.203117  0.206964   
13    0.206912  0.227292  0.161471  0.192331  0.179776  0.146251  0.182298   
14    0.192059  0.231666  0.162523  0.166163  0.219403  0.203368  0.198386   
15    0.188581  0.212237  0.166787  0.202983  0.226658  0.148462  0.186136   
16    0.187146  0.200012  0.190982  0.135995  0.218887  0.184911  0.210660   
17    0.178618  0.198443  0.172438  0.173707  0.170493  0.168867  0.181903   
18    0.139755  0.139415  0.132076  0.171903  0.146886  0.106474  0.121075   
19    0.231389  0.202586  0.223090  0.185778  0.189354  0.200669  0.205661   
20    0.238473  0.174035  0.195982  0.165292  0.126519  0.191500  0.163493   
21    0.184828  0.135552  0.176471  0.124099  0.186136  0.114875  0.147527   
22    0.196762  0.168104  0.190338  0.158419  0.184313  0.171973  0.181014   
23    0.162597  0.153418  0.163990  0.185206  0.182167  0.127652  0.200366   
24    0.189908  0.177710  0.175343  0.165603  0.176787  0.155646  0.191853   
25    0.236452  0.229133  0.256697  0.138305  0.202665  0.206538  0.220038   
26    0.275748  0.232946  0.278533  0.190133  0.212006  0.204673  0.219260   
27    0.214548  0.200676  0.201098  0.221107  0.224908  0.182626  0.214390   
28    0.160276  0.187871  0.158109  0.200751  0.183175  0.137928  0.147727   
29    0.201526  0.171134  0.225140  0.135542  0.129939  0.179308  0.166532   
30    0.222019  0.228651  0.255896  0.182558  0.224710  0.226068  0.217135   
31    0.230756  0.245406  0.190252  0.181380  0.206439  0.206621  0.230278   
32    0.178763  0.217923  0.187090  0.248093  0.211233  0.136289  0.231431   
33    0.196066  0.238937  0.253291  0.156652  0.203848  0.238241  0.234383   
34    0.217441  0.185259  0.207069  0.179714  0.224464  0.173948  0.217933   
35    0.150069  0.156937  0.129961  0.152079  0.162985  0.121253  0.160181   
36    0.117672  0.111179  0.123060  0.140934  0.140925  0.098832  0.121549   
37    0.218588  0.219965  0.209741  0.155138  0.201566  0.189687  0.227919   
38    0.256821  0.232034  0.261393  0.172246  0.188606  0.222961  0.227385   
39    0.225497  0.198842  0.200653  0.224833  0.210259  0.161800  0.232926   
40    0.271482  0.241715  0.269920  0.187772  0.204216  0.251399  0.255959   
41    0.228770  0.175442  0.241674  0.136219  0.208705  0.189580  0.249435   
42    0.216430  0.236175  0.194192  0.200418  0.208485  0.167657  0.191160   
43    0.226636  0.172291  0.187123  0.168520  0.194420  0.153340  0.168909   
44    0.220227  0.226842  0.185806  0.201077  0.208968  0.151283  0.199546   
45    0.188099  0.190426  0.215291  0.187007  0.196116  0.159544  0.201153   
46    0.246709  0.210936  0.262257  0.222958  0.215178  0.219387  0.227393   
47    0.186901  0.223377  0.204252  0.199256  0.193187  0.181588  0.224125   
48    0.248905  0.189748  0.218596  0.186991  0.227377  0.164820  0.218659   
49    0.197901  0.158318  0.164679  0.168862  0.177493  0.156064  0.186836   
50    0.245656  0.226204  0.2592

In [58]:
#label the dataframe with customer name correctly
cosine_sim.columns=m.index
cosine_sim.index=m.index

In [59]:
#replace the diagonal with 0 to avoid them being counted in the treshold list cuz they always equal 1
cosine_sim=cosine_sim.mask(cosine_sim == 1, 0)

In [71]:
cosine_sim

cust_id   29568     29909     39856     109693    289996    299749    \
cust_id                                                                
29568     0.000000  0.211481  0.265617  0.218605  0.189003  0.244841   
29909     0.211481  0.000000  0.229511  0.183954  0.209875  0.188116   
39856     0.265617  0.229511  0.000000  0.152898  0.196476  0.237962   
109693    0.218605  0.183954  0.152898  0.000000  0.171523  0.152504   
289996    0.189003  0.209875  0.196476  0.171523  0.000000  0.143769   
299749    0.244841  0.188116  0.237962  0.152504  0.143769  0.000000   
329968    0.230289  0.212436  0.264481  0.152074  0.203972  0.197323   
339627    0.223682  0.208603  0.222311  0.158337  0.194346  0.196598   
550000    0.254526  0.187471  0.218131  0.156570  0.203145  0.193756   
559804    0.214676  0.182193  0.196936  0.192995  0.178584  0.187363   
609881    0.191714  0.195148  0.193986  0.177482  0.131281  0.161565   
709543    0.275747  0.201915  0.229711  0.166103  0.156910  0.229315   
749556    0.258722  0.202267  0.204305  0.216512  0.182537  0.203117   
749639    0.206912  0.227292  0.161471  0.192331  0.179776  0.146251   
769883    0.192059  0.231666  0.162523  0.166163  0.219403  0.203368   
799924    0.188581  0.212237  0.166787  0.202983  0.226658  0.148462   
869947    0.187146  0.200012  0.190982  0.135995  0.218887  0.184911   
989587    0.178618  0.198443  0.172438  0.173707  0.170493  0.168867   
1049570   0.139755  0.139415  0.132076  0.171903  0.146886  0.106474   
1139738   0.231389  0.202586  0.223090  0.185778  0.189354  0.200669   
1179795   0.238473  0.174035  0.195982  0.165292  0.126519  0.191500   
1279966   0.184828  0.135552  0.176471  0.124099  0.186136  0.114875   
1329967   0.196762  0.168104  0.190338  0.158419  0.184313  0.171973   
1369576   0.162597  0.153418  0.163990  0.185206  0.182167  0.127652   
1459955   0.189908  0.177710  0.175343  0.165603  0.176787  0.155646   
1539803   0.236452  0.229133  0.256697  0.138305  0.202665  0.206538   
1589813   0.275748  0.232946  0.278533  0.190133  0.212006  0.204673   
1659549   0.214548  0.200676  0.201098  0.221107  0.224908  0.182626   
1849794   0.160276  0.187871  0.158109  0.200751  0.183175  0.137928   
1889991   0.201526  0.171134  0.225140  0.135542  0.129939  0.179308   
1979644   0.222019  0.228651  0.255896  0.182558  0.224710  0.226068   
1999671   0.230756  0.245406  0.190252  0.181380  0.206439  0.206621   
2009974   0.178763  0.217923  0.187090  0.248093  0.211233  0.136289   
2029760   0.196066  0.238937  0.253291  0.156652  0.203848  0.238241   
2039621   0.217441  0.185259  0.207069  0.179714  0.224464  0.173948   
2049977   0.150069  0.156937  0.129961  0.152079  0.162985  0.121253   
2089806   0.117672  0.111179  0.123060  0.140934  0.140925  0.098832   
2109544   0.218588  0.219965  0.209741  0.155138  0.201566  0.189687   
2169803   0.256821  0.232034  0.261393  0.172246  0.188606  0.222961   
2209804   0.225497  0.198842  0.200653  0.224833  0.210259  0.161800   
2269534   0.271482  0.241715  0.269920  0.187772  0.204216  0.251399   
2389981   0.228770  0.175442  0.241674  0.136219  0.208705  0.189580   
2469932   0.216430  0.236175  0.194192  0.200418  0.208485  0.167657   
2499933   0.226636  0.172291  0.187123  0.168520  0.194420  0.153340   
2569933   0.220227  0.226842  0.185806  0.201077  0.208968  0.151283   
2589576   0.188099  0.190426  0.215291  0.187007  0.196116  0.159544   
2629968   0.246709  0.210936  0.262257  0.222958  0.215178  0.219387   
2679893   0.186901  0.223377  0.204252  0.199256  0.193187  0.181588   
2719577   0.248905  0.189748  0.218596  0.186991  0.227377  0.164820   
2809801   0.197901  0.158318  0.164679  0.168862  0.177493  0.156064   
2899928   0.245656  0.226204  0.259238  0.184120  0.212468  0.208200   
2909908   0.186953  0.227607  0.197429  0.215672  0.196375  0.138740   
2969695   0.124665  0.138039  0.125662  0.158705  0.100351  0.159522   
3029520   0.244865  0.204857  0.286178  

In [60]:
def threshold_list(score):
    threshold=pd.DataFrame(cosine_sim>score)
    s=set()
    stack=threshold.stack()
    ii = stack[stack == True].index.tolist()
    for i in range(len(ii)):
        s.add(ii[i][0])
        s.add(ii[i][1])
    cust_l=list(s)
    return cust_l

In [61]:
#get the product bought by all the customers in the our threshold list
def get_product(cust_l):
    pro_s=set()
    for n in range(len(cust_l)):
        #one customer
        c_sub=customer[customer['cust_id']==cust_l[n]]
        #this customer's produts
        prod_l=list(c_sub['prod_id'])
        for i in range(len(prod_l)):
            pro_s.add(prod_l[i])
    return pro_s

In [70]:
len(threshold_list(0.4))

6

In [ ]:
len(get_product(threshold_list(0.35)))

In [100]:
def get_top(top):
    top_l=list()
    for n in range(len(cosine_sim)):
        top_l.append(cosine_sim.nlargest(top,cosine_sim.index[n]).index.tolist())
    return top_l

In [102]:
top_d=pd.DataFrame(get_top(3))

In [104]:
top_d.index=cosine_sim.index
top_d

0         1         2
cust_id                               
29568     24719817  40549840  54489828
29909     80899687  37989556  13129627
39856     96479520  13129627  25619583
109693    73859929   2009974  50509899
289996    99599996  58919615  23319833
299749    57069655  24719817  48179755
329968    24719817  13129627  73929558
339627    37989556  36599872   2269534
550000     2109544  98629985  76579825
559804    54489891  87959993  96319541
609881    88659885  59599958   9019561
709543    46959980  24719817  13129627
749556    23669807  91979512  96229536
749639    65289953  24149601  17799733
769883    23319645  89199579  46539981
799924    29079953  22799572   4759939
869947    21319608  41309992  48179755
989587    37989556  41459822  17929584
1049570   19379779  66439704  37489965
1139738   23669807  65039971  56969964
1179795    2169803  31139798  91219895
1279966   22869555  37059708  86219926
1329967   72369948  48439936  88019840
1369576   40099958  82309911  48029974
1459955   84659856  33119644  14509826
1539803   13129627  24719817  25619583
1589813   82719851  66789769  23669807
1659549   26349578  23009913  74209587
1849794   77609665  29629991  66099964
1889991   54999909  42939560  65029956
1979644   47389671  96779944  88149930
1999671   27999642  46539873  17329573
2009974   81239800   9019954  33169596
2029760   38339836  88589894   3689897
2039621   66789769  32989638  27989838
2049977   66019821  47739935  80179655
2089806   28389996  74629735   5209899
2109544     550000  76579825  37719816
2169803   66789769  62139531   3299585
2209804   35119545  10669538  62139531
2269534   11119662  65039971  38039576
2389981   46319846   9289880  73649581
2469932   22499552  45959960  48439936
2499933   21079546  48439936  49709559
2569933   24609776  83869839  66099964
2589576   83869839  31139798  64049949
2629968   17329573  30869611  29519813
2679893   38959697  93059807  72759832
2719577   63039914  47519827  83519590
2809801   53229603  41459822  54099615
2899928   23669807  66789769  62019817
2909908   30519968  80479816  61279763
2969695   59899635  23629919  76099948
3029520   14639599  57069655  11119662
3189829   33169596  24719817  14509826
3239920   61019724  25439651  89089557
3239931   24719817     39856   8279980
3269902   69679884  59499720  75129816
3299585   83999556   2169803  78619916
3409832    3689897   2269534  38339836
3489829   15310000   6389560  18900000
3509691   13129627  24719817  86559607
3509800   48439936  30349561   8409818
3549558   40549840   2269534  58629981
3689815   13129627  86559607  24719817
3689897   88589894  24719817  60619555
3759797   65949616  34409832  73509796
3779918   50069642  73979986  54459976
3809808     299749  77839901  86559607
3979821    8329796  73649581  77839901
4139823   31879773  25619583  17929584
4139886   48419623  92039648  83999556
4149898   54489828  85399739  13129627
4219822   80209969  96229536  14259755
4289603   97339976  95959691  90889526
4319967   40549840  48179755  66789769
4369949   48829987  66979624  44419979
4459951   88149930  58939977  91789971
4559994   54299912  73939814  42939560
4579768   98909970  30919566  47729807
4589623   21549599  24609776  41579936
4689635   28979791  49579835  79869779
4729534   13129627  33169596  65029956
4759939   34179982  81239800  80169689
4779672   27899942  80479816  93439979
4809965   93059555  28979791  32489834
4899809   46179611  58859523  47739935
5019544   33169596   2269534  82849654
5039834   10119835  96829926  55769927
5039894   80479816    749556  76579825
5059954   72759832  54339975   5209899
5069807   54489828  69679884  65039971
5089853    2909908  98729746  24179544
5209899    3689897  91219895  96229536
5369881   26349578  44629969  78339923
5429986   43509764  93589983  26159689
5669543   37989556  73509796  14079512
5749887    3689897  81679574   9879865
5929637   45289949  67089984  20009976
6019835   28979791  86219926  93059555
6139888   13129627  31139798  24719817


In [ ]:
metric='cosine'
k=4
def findksimilarusers(user_id, ratings, metric = metric, k=k):
    similarities=[]
    indices=[]
    model_knn = NearestNeighbors(metric = metric, algorithm = 'brute') 
    model_knn.fit(ratings)

    distances, indices = model_knn.kneighbors(ratings.iloc[user_id-1, :].values.reshape(1, -1), n_neighbors = k+1)
    similarities = 1-distances.flatten()
    print ('{0} most similar users for User {1}:\n'.format(k,user_id))
    for i in range(0, len(indices.flatten())):
        if indices.flatten()[i]+1 == user_id:
            continue;

        else:
            print ('{0}: User {1}, with similarity of {2}'.format(i, indices.flatten()[i]+1, similarities.flatten()[i]))
            
    return similarities,indices

In [ ]:
similarities,indices = findksimilarusers(29568,m, metric='cosine')

In [80]:
cd C:\Users\Jacky Yang\Desktop\Marketing Analytics\Recommend System

C:\Users\Jacky Yang\Desktop\Marketing Analytics\Recommend System


In [81]:
m.to_csv('m.csv')